In [ ]:
!pip install -q git+https://github.com/huggingface/transformers.git

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


In [ ]:
!pip install -q datasets sentencepiece

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 527.3/527.3 kB 26.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 8.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 39.9/39.9 MB 18.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 9.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 13.4 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
cudf-cu12 24.4.1 requires pyarrow<15.0.0a0,>=14.0.1, but you have pyarrow 17.0.0 which is incompatible.
ibis-framework 8.0.0 requires pyarrow<16,>=2, but you have pyarrow 17.0.0 which is incompatible.


In [ ]:
!pip install -q pytorch-lightning wandb

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 815.2/815.2 kB 32.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.3/9.3 MB 57.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.3/207.3 kB 15.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 309.1/309.1 kB 18.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 866.2/866.2 kB 34.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 3.3 MB/s eta 0:00:00


In [ ]:
from huggingface_hub import notebook_login

notebook_login()

In [ ]:
from datasets import load_dataset

dataset = load_dataset("indra-inc/docvqa_en_train_valid_2400_gtparse")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Generating train split:   0%|          | 0/2000 [00:00<?, ? examples/s]

Generating valid split:   0%|          | 0/400 [00:00<?, ? examples/s]

In [ ]:
dataset

DatasetDict({
    train: Dataset({
        features: ['question', 'docId', 'answers', 'data_split', 'bounding_boxes', 'word_list', 'image_raw', 'ground_truth'],
        num_rows: 2000
    })
    valid: Dataset({
        features: ['question', 'docId', 'answers', 'data_split', 'bounding_boxes', 'word_list', 'image_raw', 'ground_truth'],
        num_rows: 400
    })
})

In [ ]:
from transformers import VisionEncoderDecoderConfig

max_length = 128
image_size = [1280, 960]

config = VisionEncoderDecoderConfig.from_pretrained("naver-clova-ix/donut-base")
config.encoder.image_size = image_size # (height, width)
config.decoder.max_length = max_length

config.json:   0%|          | 0.00/4.74k [00:00<?, ?B/s]

In [ ]:
from transformers import DonutProcessor, VisionEncoderDecoderModel, BartConfig

processor = DonutProcessor.from_pretrained("naver-clova-ix/donut-base")
model = VisionEncoderDecoderModel.from_pretrained("naver-clova-ix/donut-base", config=config)

preprocessor_config.json:   0%|          | 0.00/362 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/518 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/1.30M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/4.01M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/71.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/355 [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be deprecated in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


pytorch_model.bin:   0%|          | 0.00/809M [00:00<?, ?B/s]

In [ ]:
from typing import List

def add_tokens(list_of_tokens: List[str]):
    newly_added_num = processor.tokenizer.add_tokens(list_of_tokens)
    if newly_added_num > 0:
        model.decoder.resize_token_embeddings(len(processor.tokenizer))

In [ ]:
additional_tokens = ["<yes/>", "<no/>"]

add_tokens(additional_tokens)

In [ ]:
import json
import random
from typing import Any, List, Tuple

import torch
from torch.utils.data import Dataset

added_tokens = []

class DonutDataset(Dataset):
    def __init__(
        self,
        dataset_name_or_path: str,
        max_length: int,
        split: str = "train",
        ignore_id: int = -100,
        task_start_token: str = "<s>",
        prompt_end_token: str = None,
        sort_json_key: bool = True,
    ):
        super().__init__()

        self.max_length = max_length
        self.split = split
        self.ignore_id = ignore_id
        self.task_start_token = task_start_token
        self.prompt_end_token = prompt_end_token if prompt_end_token else task_start_token
        self.sort_json_key = sort_json_key

        self.dataset = load_dataset(dataset_name_or_path, split=self.split)
        self.dataset_length = len(self.dataset)

        self.gt_token_sequences = []
        for sample in self.dataset:
          question = sample['question']
          ground_truth = json.loads(sample["ground_truth"])  # assuming ground_truth is in JSON format
          if "gt_parses" in ground_truth:
              gt_jsons = ground_truth["gt_parses"]
          else:
              gt_jsons = [{"question": question, "answer": sample["answers"][0]}]

          self.gt_token_sequences.append(
              [
                  self.json2token(
                      gt_json,
                      update_special_tokens_for_json_key=self.split == "train",
                      sort_json_key=self.sort_json_key,
                  )
                  + processor.tokenizer.eos_token
                  for gt_json in gt_jsons
              ]
          )


        self.add_tokens([self.task_start_token, self.prompt_end_token])
        self.prompt_end_token_id = processor.tokenizer.convert_tokens_to_ids(self.prompt_end_token)

    def json2token(self, obj: Any, update_special_tokens_for_json_key: bool = True, sort_json_key: bool = True):
        if type(obj) == dict:
            output = ""
            if "question" in obj and "answer" in obj:
                output += fr"<s_question>{obj['question']}</s_question>"
                output += fr"<s_answer>{obj['answer']}</s_answer>"
            else:
                for k in sorted(obj.keys(), reverse=True):
                    output += fr"<s_{k}>" + self.json2token(obj[k], update_special_tokens_for_json_key, sort_json_key) + fr"</s_{k}>"
            return output
        elif type(obj) == list:
            return r"<sep/>".join([self.json2token(item, update_special_tokens_for_json_key, sort_json_key) for item in obj])
        else:
            return str(obj)


    def add_tokens(self, list_of_tokens: List[str]):
        newly_added_num = processor.tokenizer.add_tokens(list_of_tokens)
        if newly_added_num > 0:
            model.decoder.resize_token_embeddings(len(processor.tokenizer))
            added_tokens.extend(list_of_tokens)

    def __len__(self) -> int:
        return self.dataset_length - 1

    def __getitem__(self, idx: int) -> Tuple[torch.Tensor, torch.Tensor, torch.Tensor]:
        sample = self.dataset[idx]

        # input_tensor
        pixel_values = processor(sample["image_raw"].convert("RGB"), random_padding=self.split == "train", return_tensors="pt").pixel_values
        input_tensor = pixel_values.squeeze()

        # input_ids
        processed_parse = random.choice(self.gt_token_sequences[idx])
        input_ids = processor.tokenizer(
            processed_parse,
            add_special_tokens=False,
            max_length=self.max_length,
            padding="max_length",
            truncation=True,
            return_tensors="pt",
        )["input_ids"].squeeze(0)

        if self.split == "train":
            labels = input_ids.clone()
            labels[
                labels == processor.tokenizer.pad_token_id
            ] = self.ignore_id
            labels[
                : torch.nonzero(labels == self.prompt_end_token_id).sum() + 1
            ] = self.ignore_id
            return input_tensor, input_ids, labels
        else:
            prompt_end_index = torch.nonzero(
                input_ids == self.prompt_end_token_id
            ).sum()
            return input_tensor, input_ids, prompt_end_index, processed_parse

In [ ]:
dataset

DatasetDict({
    train: Dataset({
        features: ['question', 'docId', 'answers', 'data_split', 'bounding_boxes', 'word_list', 'image_raw', 'ground_truth'],
        num_rows: 2000
    })
    valid: Dataset({
        features: ['question', 'docId', 'answers', 'data_split', 'bounding_boxes', 'word_list', 'image_raw', 'ground_truth'],
        num_rows: 400
    })
})

In [ ]:
processor.feature_extractor.size = image_size[::-1] # should be (width, height)
processor.feature_extractor.do_align_long_axis = False

train_dataset = DonutDataset("indra-inc/docvqa_en_train_valid_2400_gtparse", max_length=max_length,
                             split="train", task_start_token="<s_docvqa>", prompt_end_token="<s_answer>",
                             sort_json_key=False,
                             )

val_dataset = DonutDataset("indra-inc/docvqa_en_train_valid_2400_gtparse", max_length=max_length,
                             split="valid", task_start_token="<s_docvqa>", prompt_end_token="<s_answer>",
                             sort_json_key=False,
                             )

NameError: name 'image_size' is not defined

In [ ]:
pixel_values, decoder_input_ids, labels = train_dataset[0]

In [ ]:
pixel_values.shape

torch.Size([3, 1280, 960])

In [ ]:
print(labels)

tensor([ -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
         -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
         -100,  -100,  -100,  1314, 27810, 47106,  4050, 40598, 46192, 41403,
          355, 47680, 34791,     2,  -100,  -100,  -100,  -100,  -100,  -100,
         -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
         -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
         -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
         -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
         -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
         -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
         -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
         -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
         -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100])

In [ ]:
for decoder_input_id, label in zip(decoder_input_ids.tolist()[:-1], labels.tolist()[1:]):
  if label != -100:
    print(processor.decode([decoder_input_id]), processor.decode([label]))
  else:
    print(processor.decode([decoder_input_id]), label)

< -100
s -100
_ -100
ques -100
tion -100
> -100
what -100
is -100
the -100
date -100
mention -100
ed -100
in -100
this -100
letter -100
? -100
</ -100
s -100
_ -100
ques -100
tion -100
> -100
<s_answer> 1
1 /8
/8 /
/ 93
93 </
</ s
s _
_ ans
ans wer
wer >
> </s>
</s> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<pad> -100
<p

In [ ]:
pixel_values, decoder_input_ids, prompt_end_index, answer = val_dataset[0]

In [ ]:
pixel_values.shape

torch.Size([3, 1280, 960])

In [ ]:
prompt_end_index

tensor(28)

In [ ]:
answer

'<s_question>What is the ‘actual’ value per 1000, during the year 1975?</s_question><s_answer>0.28</s_answer></s>'

In [ ]:
from torch.utils.data import DataLoader

train_dataloader = DataLoader(train_dataset, batch_size=1, shuffle=True, num_workers=4)
val_dataloader = DataLoader(val_dataset, batch_size=1, shuffle=False, num_workers=4)

/usr/local/lib/python3.10/dist-packages/torch/utils/data/dataloader.py:558: UserWarning: This DataLoader will create 4 worker processes in total. Our suggested max number of worker in current system is 2, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  warnings.warn(_create_warning_msg(


In [ ]:
batch = next(iter(train_dataloader))
pixel_values, decoder_input_ids, labels = batch
print(pixel_values.shape)

/usr/lib/python3.10/multiprocessing/popen_fork.py:66: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = os.fork()
/usr/lib/python3.10/multiprocessing/popen_fork.py:66: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = os.fork()


torch.Size([1, 3, 1280, 960])


In [ ]:
decoder_input_ids.shape

torch.Size([1, 128])

In [ ]:
for decoder_input_id, label in zip(decoder_input_ids[0].tolist()[:-1][:30], labels[0].tolist()[1:][:30]):
  if label != -100:
    print(processor.decode([decoder_input_id]), processor.decode([label]))
  else:
    print(processor.decode([decoder_input_id]), label)

< -100
s -100
_ -100
ques -100
tion -100
> -100
What -100
is -100
the -100
date -100
in -100
the -100
memor -100
a -100
ndum -100
? -100
</ -100
s -100
_ -100
ques -100
tion -100
> -100
<s_answer> January
January 18
18 ,
, 1977
1977 </
</ s
s _
_ ans


In [ ]:
from pathlib import Path
import re
from nltk import edit_distance
import numpy as np
import math
import torch
from torch.nn.utils.rnn import pad_sequence

import pytorch_lightning as pl


class DonutModelPLModule(pl.LightningModule):
    def __init__(self, config, processor, model):
        super().__init__()
        self.config = config
        self.processor = processor
        self.model = model
        self.validation_scores = []  # List to store validation scores

    def training_step(self, batch, batch_idx):
        pixel_values, decoder_input_ids, labels = batch

        outputs = self.model(pixel_values,
                             decoder_input_ids=decoder_input_ids[:, :-1],
                             labels=labels[:, 1:])
        loss = outputs.loss
        self.log_dict({"train_loss": loss}, sync_dist=True)
        return loss

    def validation_step(self, batch, batch_idx):
        pixel_values, decoder_input_ids, prompt_end_idxs, answers = batch
        decoder_prompts = pad_sequence(
            [input_id[: end_idx + 1] for input_id, end_idx in zip(decoder_input_ids, prompt_end_idxs)],
            batch_first=True,
        )

        outputs = self.model.generate(pixel_values,
                                   decoder_input_ids=decoder_prompts,
                                   max_length=self.config.get("max_length", 128),
                                   early_stopping=True,
                                   pad_token_id=self.processor.tokenizer.pad_token_id,
                                   eos_token_id=self.processor.tokenizer.eos_token_id,
                                   use_cache=True,
                                   num_beams=1,
                                   bad_words_ids=[[self.processor.tokenizer.unk_token_id]],
                                   return_dict_in_generate=True,)

        predictions = []
        for seq in self.processor.tokenizer.batch_decode(outputs.sequences):
            seq = seq.replace(self.processor.tokenizer.eos_token, "").replace(self.processor.tokenizer.pad_token, "")
            seq = re.sub(r"<.*?>", "", seq, count=1).strip()
            predictions.append(seq)

        scores = []
        for pred, answer in zip(predictions, answers):
            pred = re.sub(r"(?:(?<=>) | (?=</s_))", "", pred)
            answer = re.sub(r"<.*?>", "", answer, count=1)
            answer = answer.replace(self.processor.tokenizer.eos_token, "")
            scores.append(edit_distance(pred, answer) / max(len(pred), len(answer)))

            if self.config.get("verbose", False) and len(scores) == 1:
                print(f"Prediction: {pred}")
                print(f"    Answer: {answer}")
                print(f" Normed ED: {scores[0]}")

        return {"scores": scores}

    def on_validation_epoch_end(self):
        if not self.validation_scores:
            return

        all_scores = []
        for batch_scores in self.validation_scores:
            all_scores.extend(batch_scores['scores'])

        cnt = len(all_scores)
        if cnt > 0:
            avg_metric = np.sum(all_scores) / cnt
            self.log_dict({"val_metric": avg_metric}, sync_dist=True)
        else:
            self.log_dict({"val_metric": 0}, sync_dist=True)

    def configure_optimizers(self):
        optimizer = torch.optim.Adam(self.parameters(), lr=self.config.get("lr"))
        return optimizer

    def train_dataloader(self):
        return train_dataloader

    def val_dataloader(self):
        return val_dataloader

    def on_train_start(self):
        self.validation_scores = []

    def on_validation_epoch_start(self):
        self.validation_scores = []

    def on_validation_end(self):
        pass


In [ ]:
config = {"max_epochs":10,
          "val_check_interval":0.2,
          "check_val_every_n_epoch":1,
          "gradient_clip_val":1.0,
          "num_training_samples_per_epoch": 800,
          "lr":3e-5,
          "train_batch_sizes": [8],
          "val_batch_sizes": [1],
          # "seed":2022,
          "num_nodes": 1,
          "warmup_steps": 300, # 800/8*30/10, 10%
          "result_path": "./result",
          "verbose": True,
          }

model_module = DonutModelPLModule(config, processor, model)

In [ ]:
from pytorch_lightning.loggers import WandbLogger

wandb_logger = WandbLogger(project="Donut-DocVQA")

trainer = pl.Trainer(
        accelerator="gpu",
        devices=1,
        max_epochs=config.get("max_epochs"),
        val_check_interval=config.get("val_check_interval"),
        check_val_every_n_epoch=config.get("check_val_every_n_epoch"),
        gradient_clip_val=config.get("gradient_clip_val"),
        precision=16, # we'll use mixed precision
        num_sanity_val_steps=0,
        logger=wandb_logger,
        # callbacks=[lr_callback, checkpoint_callback],
)

trainer.fit(model_module)

/usr/local/lib/python3.10/dist-packages/lightning_fabric/connector.py:571: `precision=16` is supported for historical reasons but its usage is discouraged. Please set your precision to 16-mixed instead!
INFO:pytorch_lightning.utilities.rank_zero:Using 16bit Automatic Mixed Precision (AMP)
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

 ··········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


...

Validation: |          | 0/? [00:00<?, ?it/s]

Prediction: What is the ‘actual’ value per 1000, during the year 1975?</s_question><s_answer>1983</s_answer>
    Answer: What is the ‘actual’ value per 1000, during the year 1975?</s_question><s_answer>0.28</s_answer>
 Normed ED: 0.041666666666666664
Prediction: What is name of university?</s_question><s_answer>California San Diego</s_answer>
    Answer: What is name of university?</s_question><s_answer>university of california</s_answer>
 Normed ED: 0.23529411764705882
Prediction: What is the name of the company?</s_question><s_answer>U.S.B.A.</s_answer>
    Answer: What is the name of the company?</s_question><s_answer>itc limited</s_answer>
 Normed ED: 0.14285714285714285
Prediction: Where is the university located?</s_question><s_answer>Washington</s_answer>
    Answer: Where is the university located ?</s_question><s_answer>San Diego</s_answer>
 Normed ED: 0.10526315789473684
Prediction: To whom is the document sent?</s_question><s_answer>Mr.</s_answer>
    Answer: To whom is the 

Validation: |          | 0/? [00:00<?, ?it/s]

Prediction: What is the ‘actual’ value per 1000, during the year 1975?</s_question><s_answer>1983</s_answer>
    Answer: What is the ‘actual’ value per 1000, during the year 1975?</s_question><s_answer>0.28</s_answer>
 Normed ED: 0.041666666666666664
Prediction: What is name of university?</s_question><s_answer>California</s_answer>
    Answer: What is name of university?</s_question><s_answer>university of california</s_answer>
 Normed ED: 0.17647058823529413
Prediction: What is the name of the company?</s_question><s_answer>INTRODUCTION AECOLY STUDIES</s_answer>
    Answer: What is the name of the company?</s_question><s_answer>itc limited</s_answer>
 Normed ED: 0.27956989247311825
Prediction: Where is the university located?</s_question><s_answer>University of California</s_answer>
    Answer: Where is the university located ?</s_question><s_answer>San Diego</s_answer>
 Normed ED: 0.25555555555555554
Prediction: To whom is the document sent?</s_question><s_answer>WHILE YOU WERE OUT<

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=10` reached.


In [ ]:
repo_name = "fairuzafnan/donut-docvqa"

model_module.processor.push_to_hub(repo_name)
model_module.model.push_to_hub(repo_name)

sentencepiece.bpe.model:   0%|          | 0.00/1.30M [00:00<?, ?B/s]

README.md:   0%|          | 0.00/5.17k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/809M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/fairuzafnan/donut-docvqa/commit/b0b56413d09d41b6e5c4ba44eb2b49e49e7d4f12', commit_message='Upload model', commit_description='', oid='b0b56413d09d41b6e5c4ba44eb2b49e49e7d4f12', pr_url=None, pr_revision=None, pr_num=None)